In [298]:
import catboost
import lightgbm as lgb
import matplotlib.pyplot as plt
import numpy as np
import os
import pandas as pd
import seaborn as sns
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import MinMaxScaler
from tqdm import tqdm
import pandas as pd
from sklearn.metrics import mean_absolute_error
from copy import deepcopy
sns.set()

In [299]:
X_train = pd.read_csv('lt_train.csv')
X_test = pd.read_csv('lt_test.csv')

In [300]:
X_train.describe()

location_id     product_id         demand   PROMO1_FLAG  \
count  402902.000000  402902.000000  249593.000000  3.402342e+06   
mean      866.363049   68773.279194       0.381047  4.085950e-01   
std       339.571497   27970.451505       0.690858  5.081324e-01   
min       309.000000   23252.000000       0.000000  0.000000e+00   
25%       557.000000   37466.000000       0.033175  0.000000e+00   
50%       798.000000   76559.000000       0.090909  0.000000e+00   
75%      1191.000000   88915.000000       0.466667  1.000000e+00   
max      1380.000000  149517.000000      27.000000  3.000000e+00   

        PROMO2_FLAG  PRICE_REGULAR  PRICE_AFTER_DISC  NUM_CONSULTANT  \
count  3.402342e+06   2.182591e+06      2.147736e+06    3.402342e+06   
mean   1.626821e-03   2.256149e+03      1.488290e+03    1.222108e-01   
std    4.030105e-02   5.514987e+02      4.408112e+02    7.633092e-01   
min    0.000000e+00   4.950000e+02      9.900000e-01    0.000000e+00   
25%    0.000000e+00   1.999000e+03      1.181250e+03    0.000000e+00   
50%    0.000000e+00   2.399000e+03      1.434414e+03    0.000000e+00   
75%    0.000000e+00   2.600000e+03      1.762500e+03    0.000000e+00   
max    1.000000e+00   5.699000e+03      5.449000e+03    1.100000e+01   

       AUTORIZATION_FLAG            id  
count       3.402342e+06  3.404846e+06  
mean        7.714183e-01  1.707302e+06  
std         4.199192e-01  9.833387e+05  
min         0.000000e+00  1.000000e+00  
25%         1.000000e+00  8.563642e+05  
50%         1.000000e+00  1.707576e+06  
75%         1.000000e+00  2.558787e+06  
max         1.000000e+00  3.409998e+06

In [301]:
X_train['Date'] = pd.to_datetime(X_train['period_dt'], dayfirst = True)
X_train.set_index(['Date'], inplace=True)
X_train.drop('period_dt', axis=1, inplace=True)
X_train.head()

location_id  product_id  demand  PROMO1_FLAG  PROMO2_FLAG  \
Date                                                                    
2019-12-16        764.0     23285.0     NaN          0.0          0.0   
2019-12-30        764.0     23285.0     NaN          0.0          0.0   
2019-12-09        764.0     23285.0     NaN          0.0          0.0   
2019-12-02        453.0     23285.0     NaN          1.0          0.0   
2019-12-02        764.0     23285.0     NaN          1.0          0.0   

            PRICE_REGULAR  PRICE_AFTER_DISC  NUM_CONSULTANT  \
Date                                                          
2019-12-16         2199.0            1099.5             0.0   
2019-12-30         2199.0            1099.5             0.0   
2019-12-09         2199.0            1099.5             0.0   
2019-12-02         2199.0            1319.4             0.0   
2019-12-02         2199.0            1099.5             0.0   

            AUTORIZATION_FLAG  id  
Date                               
2019-12-16                1.0   1  
2019-12-30                1.0   3  
2019-12-09                0.0   4  
2019-12-02                1.0   5  
2019-12-02                0.0   6

In [302]:
data = X_train.reset_index().copy(deep = True)

data["monthday"] = data.Date.dt.day
data["month"] = data.Date.dt.month
data["year"] = data.Date.dt.year

In [303]:
data = data.assign(ln_demand = np.log(data['demand'] + 1))
data

Date  location_id  product_id  demand  PROMO1_FLAG  PROMO2_FLAG  \
0       2019-12-16        764.0     23285.0     NaN          0.0          0.0   
1       2019-12-30        764.0     23285.0     NaN          0.0          0.0   
2       2019-12-09        764.0     23285.0     NaN          0.0          0.0   
3       2019-12-02        453.0     23285.0     NaN          1.0          0.0   
4       2019-12-02        764.0     23285.0     NaN          1.0          0.0   
...            ...          ...         ...     ...          ...          ...   
3404841 2019-12-30          NaN         NaN     NaN          1.0          0.0   
3404842 2019-12-30          NaN         NaN     NaN          1.0          0.0   
3404843 2019-12-30          NaN         NaN     NaN          1.0          0.0   
3404844 2019-12-30          NaN         NaN     NaN          1.0          0.0   
3404845 2019-12-30          NaN         NaN     NaN          1.0          0.0   

         PRICE_REGULAR  PRICE_AFTER_DISC  NUM_CONSULTANT  AUTORIZATION_FLAG  \
0               2199.0            1099.5             0.0                1.0   
1               2199.0            1099.5             0.0                1.0   
2               2199.0            1099.5             0.0                0.0   
3               2199.0            1319.4             0.0                1.0   
4               2199.0            1099.5             0.0                0.0   
...                ...               ...             ...                ...   
3404841            NaN               NaN             0.0                0.0   
3404842            NaN               NaN             0.0                0.0   
3404843            NaN               NaN             0.0                0.0   
3404844            NaN               NaN             0.0                0.0   
3404845            NaN               NaN             0.0                0.0   

              id  monthday  month  year  ln_demand  
0              1        16     12  2019        NaN  
1              3        30     12  2019        NaN  
2              4         9     12  2019        NaN  
3              5         2     12  2019        NaN  
4              6         2     12  2019        NaN  
...          ...       ...    ...   ...        ...  
3404841  3409994        30     12  2019        NaN  
3404842  3409995        30     12  2019        NaN  
3404843  3409996        30     12  2019        NaN  
3404844  3409997        30     12  2019        NaN  
3404845  3409998        30     12  2019        NaN  

[3404846 rows x 15 columns]

In [304]:
data.drop('Date', axis=1, inplace=True)

In [305]:
data['demand'] = data['demand'].fillna(-10)
data = data.fillna(0)
sc = MinMaxScaler()
sc.fit(data.iloc[:, 3:9])
data.iloc[:, 3:9] = sc.transform(data.iloc[:, 3:9])
le = LabelEncoder()
le.fit(data['location_id'])
data['location_id'] = le.transform(data['location_id'])
le.fit(data['product_id'])
data['product_id'] = le.transform(data['product_id'])
data_test = data
data = data.loc[data['demand'] > -1]

In [306]:
data_new_id = []

for i in tqdm(range(1, 42)):
    data_0 = data[(data['location_id'] == i)]
    news = data_0['product_id'].tolist()
    for j in range(1, len(news)):
        if j in news:
            data_1 = data_0[(data_0['product_id'] == j)]
            if data_1.shape[0] < 10:
                data_new_id.extend(data_1['id'].tolist())
            else:
                data_1 = data_1.loc[0:10, :]
                data_new_id.extend(data_1['id'].tolist())

100%|██████████| 41/41 [00:46<00:00,  1.13s/it]


In [307]:
len(data_new_id)

50570

In [308]:
data = data[data['id'].isin(data_new_id)]
data.describe()

location_id    product_id        demand   PROMO1_FLAG   PROMO2_FLAG  \
count  50570.000000  50570.000000  50570.000000  50570.000000  50570.000000   
mean      22.314178   1153.500356      0.710086      0.201358      0.010322   
std       11.769347    643.128291      0.929250      0.174085      0.101074   
min        1.000000      1.000000      0.000000      0.000000      0.000000   
25%       14.000000    540.000000      0.036458      0.000000      0.000000   
50%       22.000000   1208.000000      0.700000      0.333333      0.000000   
75%       34.000000   1687.000000      1.000000      0.333333      0.000000   
max       40.000000   2633.000000     27.000000      1.000000      1.000000   

       PRICE_REGULAR  PRICE_AFTER_DISC  NUM_CONSULTANT  AUTORIZATION_FLAG  \
count   50570.000000      50570.000000    50570.000000       50570.000000   
mean        0.352755          0.239304        0.010757           0.810698   
std         0.144984          0.105193        0.069655           0.391752   
min         0.000000          0.000000        0.000000           0.000000   
25%         0.306896          0.201872        0.000000           1.000000   
50%         0.412178          0.243072        0.000000           1.000000   
75%         0.456045          0.310161        0.000000           1.000000   
max         1.000000          0.770600        0.636364           1.000000   

                  id      monthday         month          year     ln_demand  
count   50570.000000  50570.000000  50570.000000  50570.000000  50570.000000  
mean   196790.638007     14.998695      6.792407   2017.545086      0.444650  
std    110928.617177      9.550371      4.094386      0.546801      0.402872  
min         7.000000      1.000000      1.000000   2016.000000      0.000000  
25%     99355.250000      6.000000      3.000000   2017.000000      0.035809  
50%    200107.500000     15.000000      7.000000   2018.000000      0.530628  
75%    285248.750000     24.000000     11.000000   2018.000000      0.693147  
max    407315.000000     31.000000     12.000000   2018.000000      3.332205

In [309]:
test_id_list = X_test['id'].tolist()

In [260]:
def CV(X_train, y_train, number_folds, model, metrics):

    k = int(np.floor(float(X_train.shape[0]) / number_folds))

    errors = np.zeros(number_folds-1)
 
    for i in range(2, number_folds + 1):

        split = float(i-1)/i

        X = X_train[:(k*i)]
        y = y_train[:(k*i)]

        index = int(np.floor(X.shape[0] * split))
       
        X_trainFolds = X[:index]        
        y_trainFolds = y[:index]

        X_testFold = X[(index + 1):]
        y_testFold = y[(index + 1):]

        model.fit(X_trainFolds, y_trainFolds, eval_set=[(X_testFold, y_testFold)])
        errors[i-2] = metrics(model.predict(X_testFold), y_testFold)
    
    return errors.mean()

In [310]:
def CV(X_train, y_train, number_folds, model, metrics, kwargs={}):

    k = int(np.floor(float(X_train.shape[0]) / number_folds))

    errors = np.zeros(number_folds-1)
 
    for i in range(2, number_folds + 1):
        print('')
        split = float(i-1)/i

        X = X_train[:(k*i)]
        y = y_train[:(k*i)]

        index = int(np.floor(X.shape[0] * split))
       
        X_trainFolds = X[:index]        
        y_trainFolds = y[:index]

        X_testFold = X[(index + 1):]
        y_testFold = y[(index + 1):]

        model.fit(X_trainFolds, y_trainFolds, **kwargs, eval_set=[(X_testFold, y_testFold)])
        errors[i-2] = metrics(model.predict(X_testFold), y_testFold)
    
    return errors.mean()

In [311]:
data.drop('demand', axis=1, inplace=True)

In [312]:
lgbm = lgb.LGBMRegressor(
                        n_estimators=350,
                        learning_rate=0.1,
                        feature_fraction=0.7,
                        subsample=0.4,
                        num_leaves=40)    

kwargs={'early_stopping_rounds':10,'verbose':2}

In [288]:
from catboost import CatBoostRegressor

ctb = CatBoostRegressor(loss_function = 'MAE',
                       early_stopping_rounds=30)

In [313]:
data_test = data_test[data_test['id'].isin(test_id_list)]

In [314]:
sub = pd.DataFrame({'id': [], 'demand': []})

In [291]:
for i in tqdm(range(2, 41)):
    data1 = data[(data['location_id'] == i)]
    data_test1 = data_test[(data_test['location_id'] == i)]
    if data_test1.shape[0] > 0:
        CV(data1.drop(['id','ln_demand', 'location_id'], axis=1),
           data1.ln_demand,
           10, ctb, mean_absolute_error)
        final_pred = ctb.predict(data_test1.drop(['id', 'demand', 'ln_demand', 'location_id'], axis=1))
        sub1 = pd.DataFrame({'id': data_test1['id'].tolist(), 'demand': final_pred})
        sub = pd.concat([sub, sub1], ignore_index=False)

  0%|          | 0/39 [00:00<?, ?it/s]

0:	learn: 0.2391499	test: 0.4570583	best: 0.4570583 (0)	total: 683us	remaining: 683ms
1:	learn: 0.2350973	test: 0.4494894	best: 0.4494894 (1)	total: 1.37ms	remaining: 685ms
2:	learn: 0.2299254	test: 0.4481470	best: 0.4481470 (2)	total: 1.97ms	remaining: 654ms
3:	learn: 0.2273786	test: 0.4503054	best: 0.4481470 (2)	total: 2.6ms	remaining: 646ms
4:	learn: 0.2236629	test: 0.4498373	best: 0.4481470 (2)	total: 3.14ms	remaining: 625ms
5:	learn: 0.2204072	test: 0.4434265	best: 0.4434265 (5)	total: 3.73ms	remaining: 618ms
6:	learn: 0.2156423	test: 0.4368099	best: 0.4368099 (6)	total: 4.36ms	remaining: 618ms
7:	learn: 0.2118075	test: 0.4327544	best: 0.4327544 (7)	total: 5.18ms	remaining: 643ms
8:	learn: 0.2083963	test: 0.4295210	best: 0.4295210 (8)	total: 5.85ms	remaining: 645ms
9:	learn: 0.2069555	test: 0.4263254	best: 0.4263254 (9)	total: 6.22ms	remaining: 616ms
10:	learn: 0.2032843	test: 0.4240725	best: 0.4240725 (10)	total: 6.8ms	remaining: 612ms
11:	learn: 0.2008998	test: 0.4170093	best: 0

245:	learn: 0.0337531	test: 0.2991734	best: 0.2991734 (245)	total: 124ms	remaining: 379ms
246:	learn: 0.0335416	test: 0.2986273	best: 0.2986273 (246)	total: 124ms	remaining: 379ms
247:	learn: 0.0333625	test: 0.2986736	best: 0.2986273 (246)	total: 125ms	remaining: 378ms
248:	learn: 0.0333301	test: 0.2986632	best: 0.2986273 (246)	total: 125ms	remaining: 377ms
249:	learn: 0.0328309	test: 0.2986022	best: 0.2986022 (249)	total: 126ms	remaining: 377ms
250:	learn: 0.0324890	test: 0.2985125	best: 0.2985125 (250)	total: 126ms	remaining: 377ms
251:	learn: 0.0324547	test: 0.2985220	best: 0.2985125 (250)	total: 127ms	remaining: 376ms
252:	learn: 0.0322231	test: 0.2985215	best: 0.2985125 (250)	total: 127ms	remaining: 376ms
253:	learn: 0.0319641	test: 0.2984680	best: 0.2984680 (253)	total: 128ms	remaining: 375ms
254:	learn: 0.0318830	test: 0.2984514	best: 0.2984514 (254)	total: 128ms	remaining: 375ms
255:	learn: 0.0316537	test: 0.2982711	best: 0.2982711 (255)	total: 129ms	remaining: 374ms
256:	learn

0:	learn: 0.3444887	test: 0.3704185	best: 0.3704185 (0)	total: 709us	remaining: 709ms
1:	learn: 0.3382773	test: 0.3657550	best: 0.3657550 (1)	total: 1.29ms	remaining: 645ms
2:	learn: 0.3326971	test: 0.3620363	best: 0.3620363 (2)	total: 1.84ms	remaining: 613ms
3:	learn: 0.3273375	test: 0.3566105	best: 0.3566105 (3)	total: 2.39ms	remaining: 596ms
4:	learn: 0.3231712	test: 0.3534199	best: 0.3534199 (4)	total: 2.81ms	remaining: 559ms
5:	learn: 0.3181974	test: 0.3498563	best: 0.3498563 (5)	total: 3.66ms	remaining: 607ms
6:	learn: 0.3130309	test: 0.3477922	best: 0.3477922 (6)	total: 4.31ms	remaining: 612ms
7:	learn: 0.3080415	test: 0.3451867	best: 0.3451867 (7)	total: 4.96ms	remaining: 615ms
8:	learn: 0.3025219	test: 0.3421812	best: 0.3421812 (8)	total: 5.63ms	remaining: 620ms
9:	learn: 0.2975846	test: 0.3373811	best: 0.3373811 (9)	total: 6.27ms	remaining: 620ms
10:	learn: 0.2925768	test: 0.3343673	best: 0.3343673 (10)	total: 6.93ms	remaining: 623ms
11:	learn: 0.2877492	test: 0.3311951	best:

219:	learn: 0.0469139	test: 0.2256983	best: 0.2250553 (191)	total: 130ms	remaining: 461ms
220:	learn: 0.0466498	test: 0.2257113	best: 0.2250553 (191)	total: 131ms	remaining: 461ms
221:	learn: 0.0465122	test: 0.2256909	best: 0.2250553 (191)	total: 131ms	remaining: 460ms
Stopped by overfitting detector  (30 iterations wait)

bestTest = 0.2250552578
bestIteration = 191

Shrink model to first 192 iterations.
0:	learn: 0.3341347	test: 0.4368917	best: 0.4368917 (0)	total: 737us	remaining: 737ms
1:	learn: 0.3297859	test: 0.4345732	best: 0.4345732 (1)	total: 1.36ms	remaining: 678ms
2:	learn: 0.3239860	test: 0.4302925	best: 0.4302925 (2)	total: 1.95ms	remaining: 647ms
3:	learn: 0.3180332	test: 0.4257090	best: 0.4257090 (3)	total: 2.49ms	remaining: 621ms
4:	learn: 0.3127580	test: 0.4244398	best: 0.4244398 (4)	total: 3.06ms	remaining: 609ms
5:	learn: 0.3081124	test: 0.4227292	best: 0.4227292 (5)	total: 3.65ms	remaining: 605ms
6:	learn: 0.3024870	test: 0.4165579	best: 0.4165579 (6)	total: 4.24ms	r

...

151:	learn: 0.1195354	test: 0.1780552	best: 0.1780552 (151)	total: 278ms	remaining: 1.55s
152:	learn: 0.1195052	test: 0.1780370	best: 0.1780370 (152)	total: 280ms	remaining: 1.55s
153:	learn: 0.1193464	test: 0.1778967	best: 0.1778967 (153)	total: 282ms	remaining: 1.55s
154:	learn: 0.1193187	test: 0.1778731	best: 0.1778731 (154)	total: 283ms	remaining: 1.54s
155:	learn: 0.1192730	test: 0.1778306	best: 0.1778306 (155)	total: 286ms	remaining: 1.54s
156:	learn: 0.1192076	test: 0.1777921	best: 0.1777921 (156)	total: 287ms	remaining: 1.54s
157:	learn: 0.1191233	test: 0.1777314	best: 0.1777314 (157)	total: 289ms	remaining: 1.54s
158:	learn: 0.1190689	test: 0.1776921	best: 0.1776921 (158)	total: 291ms	remaining: 1.54s
159:	learn: 0.1187567	test: 0.1772874	best: 0.1772874 (159)	total: 293ms	remaining: 1.54s
160:	learn: 0.1184196	test: 0.1768349	best: 0.1768349 (160)	total: 295ms	remaining: 1.54s
161:	learn: 0.1183930	test: 0.1768251	best: 0.1768251 (161)	total: 297ms	remaining: 1.54s
162:	learn

292:	learn: 0.1104471	test: 0.1681384	best: 0.1681384 (292)	total: 595ms	remaining: 1.43s
293:	learn: 0.1103545	test: 0.1681243	best: 0.1681243 (293)	total: 597ms	remaining: 1.43s
294:	learn: 0.1103441	test: 0.1681007	best: 0.1681007 (294)	total: 599ms	remaining: 1.43s
295:	learn: 0.1103190	test: 0.1680545	best: 0.1680545 (295)	total: 602ms	remaining: 1.43s
296:	learn: 0.1102516	test: 0.1680499	best: 0.1680499 (296)	total: 604ms	remaining: 1.43s
297:	learn: 0.1102338	test: 0.1680358	best: 0.1680358 (297)	total: 606ms	remaining: 1.43s
298:	learn: 0.1102314	test: 0.1680368	best: 0.1680358 (297)	total: 608ms	remaining: 1.43s
299:	learn: 0.1101783	test: 0.1680253	best: 0.1680253 (299)	total: 610ms	remaining: 1.42s
300:	learn: 0.1101564	test: 0.1679875	best: 0.1679875 (300)	total: 613ms	remaining: 1.42s
301:	learn: 0.1101474	test: 0.1679854	best: 0.1679854 (301)	total: 615ms	remaining: 1.42s
302:	learn: 0.1099380	test: 0.1678080	best: 0.1678080 (302)	total: 617ms	remaining: 1.42s
303:	learn

432:	learn: 0.1009477	test: 0.1584753	best: 0.1583698 (430)	total: 898ms	remaining: 1.18s
433:	learn: 0.1009014	test: 0.1584753	best: 0.1583698 (430)	total: 900ms	remaining: 1.17s
434:	learn: 0.1008988	test: 0.1584754	best: 0.1583698 (430)	total: 902ms	remaining: 1.17s
435:	learn: 0.1008668	test: 0.1584695	best: 0.1583698 (430)	total: 904ms	remaining: 1.17s
436:	learn: 0.1008222	test: 0.1584555	best: 0.1583698 (430)	total: 906ms	remaining: 1.17s
437:	learn: 0.1008056	test: 0.1584629	best: 0.1583698 (430)	total: 908ms	remaining: 1.17s
438:	learn: 0.1007478	test: 0.1584530	best: 0.1583698 (430)	total: 910ms	remaining: 1.16s
439:	learn: 0.1006151	test: 0.1584442	best: 0.1583698 (430)	total: 912ms	remaining: 1.16s
440:	learn: 0.1005765	test: 0.1584121	best: 0.1583698 (430)	total: 914ms	remaining: 1.16s
441:	learn: 0.1005468	test: 0.1583895	best: 0.1583698 (430)	total: 916ms	remaining: 1.16s
442:	learn: 0.1004485	test: 0.1585195	best: 0.1583698 (430)	total: 918ms	remaining: 1.15s
443:	learn

100%|██████████| 39/39 [02:13<00:00,  3.43s/it]

590:	learn: 0.0948041	test: 0.1548557	best: 0.1548557 (590)	total: 1.21s	remaining: 839ms
591:	learn: 0.0947841	test: 0.1548365	best: 0.1548365 (591)	total: 1.21s	remaining: 836ms
592:	learn: 0.0946908	test: 0.1548345	best: 0.1548345 (592)	total: 1.22s	remaining: 834ms
593:	learn: 0.0946608	test: 0.1548371	best: 0.1548345 (592)	total: 1.22s	remaining: 832ms
594:	learn: 0.0946358	test: 0.1547526	best: 0.1547526 (594)	total: 1.22s	remaining: 830ms
595:	learn: 0.0946125	test: 0.1547511	best: 0.1547511 (595)	total: 1.22s	remaining: 828ms
596:	learn: 0.0945579	test: 0.1547264	best: 0.1547264 (596)	total: 1.22s	remaining: 826ms
597:	learn: 0.0944537	test: 0.1545796	best: 0.1545796 (597)	total: 1.23s	remaining: 824ms
598:	learn: 0.0943658	test: 0.1545903	best: 0.1545796 (597)	total: 1.23s	remaining: 822ms
599:	learn: 0.0942857	test: 0.1545540	best: 0.1545540 (599)	total: 1.23s	remaining: 820ms
600:	learn: 0.0942436	test: 0.1545563	best: 0.1545540 (599)	total: 1.23s	remaining: 819ms
601:	learn

In [317]:
not_in_train = []

for i in tqdm(range(1, 2634)):
    data1 = data[(data['product_id'] == i)]
    data1 = data1.fillna(0)
    if data1.shape[0] > 0:
        data_test1 = data_test[(data_test['product_id'] == i)]
        data_test1 = data_test1.fillna(0)
        if data_test1.shape[0] > 0:
            CV(data1.drop(['id','ln_demand', 'product_id'], axis=1), data1.ln_demand, 1, lgbm, mean_absolute_error)
            final_pred = lgbm.predict(data_test1.drop(['id', 'demand', 'ln_demand', 'product_id'], axis=1))
            sub1 = pd.DataFrame({'id': data_test1['id'].tolist(), 'demand': final_pred})
            sub = pd.concat([sub, sub1], ignore_index=False)
    else:
        not_in_train.append(i)

  0%|          | 0/2633 [00:00<?, ?it/s]<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.p

  3%|▎         | 75/2633 [00:00<00:14, 175.46it/s]<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\

<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value enc

<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value enc

<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value enc

...

C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
 85%|████████▌ | 2244/2633 [00:17<00:04, 88.38it/s]<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.t

<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value enc

C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
 89%|████████▉ | 2340/2633 [00:18

C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:25: RuntimeWarning: Mean of empty slice.
  return errors.mean()
C:\Users\Lenovo\anaconda3\lib\site-packages\numpy\core\_methods.py:170: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)
<ipython-input-310-d8b5156e3871>:

100%|██████████| 2633/2633 [00:19<00:00, 137.60it/s]


In [297]:
data1 = data[(data['product_id'] == 1070)]
if data1.shape[0] > 0:
    data_test1 = data_test[(data_test['product_id'] == 1070)]
    if data_test1.shape[0] > 0:
        CV(data1.drop(['id','ln_demand', 'product_id'], axis=1), data1.ln_demand, 10, lgbm, mean_absolute_error)
        final_pred = lgbm.predict(data_test1.drop(['id', 'demand', 'ln_demand', 'product_id'], axis=1))
        sub1 = pd.DataFrame({'id': data_test1['id'].tolist(), 'demand': final_pred})
        sub = pd.concat([sub, sub1], ignore_index=False)
else:
    not_in_train.append(i)

CatBoostError: Labels variable is empty.

In [287]:
data1.drop(['id','ln_demand', 'product_id'], axis=1)

location_id  PROMO1_FLAG  PROMO2_FLAG  PRICE_REGULAR  PRICE_AFTER_DISC  \
96510            5     0.333333          0.0       0.447271          0.350844   
96511            5     0.000000          0.0       0.447271          0.350844   
96512            6     0.333333          0.0       0.447271          0.350844   
96513            9     0.333333          0.0       0.413431          0.216200   
96514            9     0.333333          0.0       0.447271          0.233896   
96515            9     0.333333          0.0       0.449778          0.235207   
96528           16     0.333333          0.0       0.447271          0.233896   
96529           16     0.000000          0.0       0.447271          0.233896   
96530           16     0.000000          0.0       0.447271          0.233896   
96531           16     0.000000          0.0       0.447271          0.233896   
96532           16     0.000000          0.0       0.447271          0.233896   
96533           16     0.000000          0.0       0.447271          0.233896   
96534           16     0.000000          0.0       0.447271          0.233896   
96545           31     0.333333          0.0       0.447271          0.350844   
96546           32     0.000000          0.0       0.000000          0.000000   

       NUM_CONSULTANT  AUTORIZATION_FLAG  monthday  month  year  
96510             0.0                1.0         2      1  2017  
96511             0.0                1.0        20      3  2017  
96512             0.0                1.0         2      1  2017  
96513             0.0                1.0        26     12  2016  
96514             0.0                1.0         2      1  2017  
96515             0.0                1.0         6     11  2017  
96528             0.0                1.0         2      1  2017  
96529             0.0                1.0         9      1  2017  
96530             0.0                1.0        16      1  2017  
96531             0.0                1.0        23      1  2017  
96532             0.0                1.0        30      1  2017  
96533             0.0                1.0         6      2  2017  
96534             0.0                1.0        13      2  2017  
96545             0.0                1.0         2      1  2017  
96546             0.0                0.0         2      1  2017

In [292]:
CV(data.drop(['id','ln_demand', 'location_id'], axis=1),
   data.ln_demand,
   10, ctb, mean_absolute_error)
data_test1 = data_test[(data_test['location_id'] == 41)]
final_pred = ctb.predict(data_test1.drop(['id', 'demand', 'ln_demand', 'location_id'], axis=1))
sub1 = pd.DataFrame({'id': data_test1['id'].tolist(), 'demand': final_pred})
sub = pd.concat([sub, sub1], ignore_index=False)

0:	learn: 0.3336593	test: 0.3453547	best: 0.3453547 (0)	total: 2.74ms	remaining: 2.74s
1:	learn: 0.3291215	test: 0.3405626	best: 0.3405626 (1)	total: 5.28ms	remaining: 2.63s
2:	learn: 0.3252169	test: 0.3364923	best: 0.3364923 (2)	total: 7.81ms	remaining: 2.6s
3:	learn: 0.3210926	test: 0.3333039	best: 0.3333039 (3)	total: 10.4ms	remaining: 2.6s
4:	learn: 0.3172026	test: 0.3291715	best: 0.3291715 (4)	total: 13ms	remaining: 2.58s
5:	learn: 0.3136398	test: 0.3260559	best: 0.3260559 (5)	total: 15.6ms	remaining: 2.59s
6:	learn: 0.3101059	test: 0.3225623	best: 0.3225623 (6)	total: 18.2ms	remaining: 2.58s
7:	learn: 0.3069634	test: 0.3195430	best: 0.3195430 (7)	total: 20.6ms	remaining: 2.56s
8:	learn: 0.3039041	test: 0.3166641	best: 0.3166641 (8)	total: 23.1ms	remaining: 2.54s
9:	learn: 0.3007360	test: 0.3136930	best: 0.3136930 (9)	total: 25.6ms	remaining: 2.54s
10:	learn: 0.2976630	test: 0.3108597	best: 0.3108597 (10)	total: 28.3ms	remaining: 2.54s
11:	learn: 0.2948137	test: 0.3077117	best: 0.

120:	learn: 0.2077216	test: 0.2288437	best: 0.2288437 (120)	total: 336ms	remaining: 2.44s
121:	learn: 0.2075520	test: 0.2287593	best: 0.2287593 (121)	total: 340ms	remaining: 2.44s
122:	learn: 0.2073721	test: 0.2286546	best: 0.2286546 (122)	total: 343ms	remaining: 2.44s
123:	learn: 0.2072787	test: 0.2286748	best: 0.2286546 (122)	total: 345ms	remaining: 2.44s
124:	learn: 0.2071374	test: 0.2286099	best: 0.2286099 (124)	total: 348ms	remaining: 2.44s
125:	learn: 0.2069723	test: 0.2285217	best: 0.2285217 (125)	total: 352ms	remaining: 2.44s
126:	learn: 0.2068064	test: 0.2283871	best: 0.2283871 (126)	total: 355ms	remaining: 2.44s
127:	learn: 0.2067487	test: 0.2284079	best: 0.2283871 (126)	total: 358ms	remaining: 2.44s
128:	learn: 0.2066750	test: 0.2283693	best: 0.2283693 (128)	total: 361ms	remaining: 2.44s
129:	learn: 0.2065742	test: 0.2283117	best: 0.2283117 (129)	total: 365ms	remaining: 2.44s
130:	learn: 0.2064502	test: 0.2282149	best: 0.2282149 (130)	total: 368ms	remaining: 2.44s
131:	learn

1:	learn: 0.3324123	test: 0.3522931	best: 0.3522931 (1)	total: 9.48ms	remaining: 4.73s
2:	learn: 0.3282639	test: 0.3483387	best: 0.3483387 (2)	total: 12.6ms	remaining: 4.2s
3:	learn: 0.3247351	test: 0.3446883	best: 0.3446883 (3)	total: 15.7ms	remaining: 3.92s
4:	learn: 0.3208308	test: 0.3413994	best: 0.3413994 (4)	total: 19.2ms	remaining: 3.83s
5:	learn: 0.3170017	test: 0.3378726	best: 0.3378726 (5)	total: 22.9ms	remaining: 3.8s
6:	learn: 0.3134741	test: 0.3344949	best: 0.3344949 (6)	total: 26.5ms	remaining: 3.75s
7:	learn: 0.3100576	test: 0.3313651	best: 0.3313651 (7)	total: 29.9ms	remaining: 3.71s
8:	learn: 0.3067950	test: 0.3281880	best: 0.3281880 (8)	total: 33.5ms	remaining: 3.69s
9:	learn: 0.3035026	test: 0.3250951	best: 0.3250951 (9)	total: 37.1ms	remaining: 3.67s
10:	learn: 0.3003577	test: 0.3221175	best: 0.3221175 (10)	total: 40.6ms	remaining: 3.65s
11:	learn: 0.2974289	test: 0.3192339	best: 0.3192339 (11)	total: 44.1ms	remaining: 3.63s
12:	learn: 0.2945992	test: 0.3165221	best

102:	learn: 0.2075219	test: 0.2379934	best: 0.2379934 (102)	total: 351ms	remaining: 3.05s
103:	learn: 0.2072966	test: 0.2378204	best: 0.2378204 (103)	total: 354ms	remaining: 3.05s
104:	learn: 0.2070858	test: 0.2377838	best: 0.2377838 (104)	total: 357ms	remaining: 3.05s
105:	learn: 0.2068710	test: 0.2376636	best: 0.2376636 (105)	total: 361ms	remaining: 3.04s
106:	learn: 0.2066473	test: 0.2375262	best: 0.2375262 (106)	total: 365ms	remaining: 3.05s
107:	learn: 0.2064049	test: 0.2372519	best: 0.2372519 (107)	total: 369ms	remaining: 3.05s
108:	learn: 0.2061937	test: 0.2371128	best: 0.2371128 (108)	total: 372ms	remaining: 3.04s
109:	learn: 0.2060062	test: 0.2370323	best: 0.2370323 (109)	total: 376ms	remaining: 3.04s
110:	learn: 0.2058284	test: 0.2369124	best: 0.2369124 (110)	total: 380ms	remaining: 3.04s
111:	learn: 0.2055739	test: 0.2366830	best: 0.2366830 (111)	total: 383ms	remaining: 3.04s
112:	learn: 0.2053857	test: 0.2365027	best: 0.2365027 (112)	total: 387ms	remaining: 3.04s
113:	learn

196:	learn: 0.1982720	test: 0.2319300	best: 0.2319300 (196)	total: 686ms	remaining: 2.79s
197:	learn: 0.1982352	test: 0.2319169	best: 0.2319169 (197)	total: 690ms	remaining: 2.79s
198:	learn: 0.1981837	test: 0.2319308	best: 0.2319169 (197)	total: 694ms	remaining: 2.79s
199:	learn: 0.1981450	test: 0.2318991	best: 0.2318991 (199)	total: 697ms	remaining: 2.79s
200:	learn: 0.1981235	test: 0.2318844	best: 0.2318844 (200)	total: 700ms	remaining: 2.78s
201:	learn: 0.1980611	test: 0.2318264	best: 0.2318264 (201)	total: 705ms	remaining: 2.78s
202:	learn: 0.1980365	test: 0.2317828	best: 0.2317828 (202)	total: 709ms	remaining: 2.78s
203:	learn: 0.1980178	test: 0.2317700	best: 0.2317700 (203)	total: 713ms	remaining: 2.78s
204:	learn: 0.1979850	test: 0.2317607	best: 0.2317607 (204)	total: 716ms	remaining: 2.78s
205:	learn: 0.1979179	test: 0.2317203	best: 0.2317203 (205)	total: 720ms	remaining: 2.77s
206:	learn: 0.1978941	test: 0.2317256	best: 0.2317203 (205)	total: 724ms	remaining: 2.77s
207:	learn

...

517:	learn: 0.2074866	test: 0.2323056	best: 0.2323056 (517)	total: 4.08s	remaining: 3.8s
518:	learn: 0.2074519	test: 0.2323431	best: 0.2323056 (517)	total: 4.09s	remaining: 3.79s
519:	learn: 0.2074200	test: 0.2323859	best: 0.2323056 (517)	total: 4.1s	remaining: 3.79s
520:	learn: 0.2073938	test: 0.2323866	best: 0.2323056 (517)	total: 4.11s	remaining: 3.78s
521:	learn: 0.2073863	test: 0.2323867	best: 0.2323056 (517)	total: 4.12s	remaining: 3.77s
522:	learn: 0.2073684	test: 0.2323799	best: 0.2323056 (517)	total: 4.12s	remaining: 3.76s
523:	learn: 0.2073314	test: 0.2323326	best: 0.2323056 (517)	total: 4.13s	remaining: 3.75s
524:	learn: 0.2073028	test: 0.2323376	best: 0.2323056 (517)	total: 4.14s	remaining: 3.74s
525:	learn: 0.2072859	test: 0.2323282	best: 0.2323056 (517)	total: 4.14s	remaining: 3.73s
526:	learn: 0.2072658	test: 0.2323250	best: 0.2323056 (517)	total: 4.15s	remaining: 3.73s
527:	learn: 0.2072209	test: 0.2323657	best: 0.2323056 (517)	total: 4.16s	remaining: 3.72s
528:	learn: 

623:	learn: 0.2057451	test: 0.2317819	best: 0.2317666 (617)	total: 4.96s	remaining: 2.99s
624:	learn: 0.2057434	test: 0.2317819	best: 0.2317666 (617)	total: 4.97s	remaining: 2.98s
625:	learn: 0.2057178	test: 0.2317795	best: 0.2317666 (617)	total: 4.98s	remaining: 2.98s
626:	learn: 0.2057152	test: 0.2317830	best: 0.2317666 (617)	total: 4.99s	remaining: 2.97s
627:	learn: 0.2056903	test: 0.2317832	best: 0.2317666 (617)	total: 5s	remaining: 2.96s
628:	learn: 0.2056885	test: 0.2317843	best: 0.2317666 (617)	total: 5.01s	remaining: 2.96s
629:	learn: 0.2056868	test: 0.2317854	best: 0.2317666 (617)	total: 5.02s	remaining: 2.95s
630:	learn: 0.2056820	test: 0.2317828	best: 0.2317666 (617)	total: 5.04s	remaining: 2.94s
631:	learn: 0.2056639	test: 0.2317427	best: 0.2317427 (631)	total: 5.04s	remaining: 2.94s
632:	learn: 0.2056558	test: 0.2317361	best: 0.2317361 (632)	total: 5.05s	remaining: 2.93s
633:	learn: 0.2056476	test: 0.2317298	best: 0.2317298 (633)	total: 5.06s	remaining: 2.92s
634:	learn: 0

716:	learn: 0.2050406	test: 0.2313600	best: 0.2313119 (691)	total: 5.66s	remaining: 2.23s
717:	learn: 0.2050319	test: 0.2313514	best: 0.2313119 (691)	total: 5.67s	remaining: 2.23s
718:	learn: 0.2050308	test: 0.2313512	best: 0.2313119 (691)	total: 5.68s	remaining: 2.22s
719:	learn: 0.2050210	test: 0.2313506	best: 0.2313119 (691)	total: 5.68s	remaining: 2.21s
720:	learn: 0.2049802	test: 0.2313117	best: 0.2313117 (720)	total: 5.69s	remaining: 2.2s
721:	learn: 0.2049757	test: 0.2313135	best: 0.2313117 (720)	total: 5.7s	remaining: 2.19s
722:	learn: 0.2049698	test: 0.2313139	best: 0.2313117 (720)	total: 5.7s	remaining: 2.19s
723:	learn: 0.2049646	test: 0.2313144	best: 0.2313117 (720)	total: 5.71s	remaining: 2.18s
724:	learn: 0.2049582	test: 0.2313161	best: 0.2313117 (720)	total: 5.72s	remaining: 2.17s
725:	learn: 0.2049528	test: 0.2313162	best: 0.2313117 (720)	total: 5.72s	remaining: 2.16s
726:	learn: 0.2049483	test: 0.2313098	best: 0.2313098 (726)	total: 5.73s	remaining: 2.15s
727:	learn: 0

817:	learn: 0.2043397	test: 0.2308678	best: 0.2308660 (813)	total: 6.36s	remaining: 1.42s
818:	learn: 0.2043213	test: 0.2308495	best: 0.2308495 (818)	total: 6.37s	remaining: 1.41s
819:	learn: 0.2043061	test: 0.2308361	best: 0.2308361 (819)	total: 6.38s	remaining: 1.4s
820:	learn: 0.2042811	test: 0.2308382	best: 0.2308361 (819)	total: 6.38s	remaining: 1.39s
821:	learn: 0.2042361	test: 0.2307299	best: 0.2307299 (821)	total: 6.39s	remaining: 1.38s
822:	learn: 0.2042354	test: 0.2307306	best: 0.2307299 (821)	total: 6.4s	remaining: 1.38s
823:	learn: 0.2041860	test: 0.2306279	best: 0.2306279 (823)	total: 6.41s	remaining: 1.37s
824:	learn: 0.2041851	test: 0.2306298	best: 0.2306279 (823)	total: 6.42s	remaining: 1.36s
825:	learn: 0.2041829	test: 0.2306299	best: 0.2306279 (823)	total: 6.42s	remaining: 1.35s
826:	learn: 0.2041815	test: 0.2306297	best: 0.2306279 (823)	total: 6.43s	remaining: 1.34s
827:	learn: 0.2041803	test: 0.2306295	best: 0.2306279 (823)	total: 6.44s	remaining: 1.34s
828:	learn: 

914:	learn: 0.2027591	test: 0.2303090	best: 0.2303090 (914)	total: 7.06s	remaining: 656ms
915:	learn: 0.2027521	test: 0.2303058	best: 0.2303058 (915)	total: 7.07s	remaining: 648ms
916:	learn: 0.2027504	test: 0.2303027	best: 0.2303027 (916)	total: 7.07s	remaining: 640ms
917:	learn: 0.2027479	test: 0.2303035	best: 0.2303027 (916)	total: 7.08s	remaining: 633ms
918:	learn: 0.2027062	test: 0.2302495	best: 0.2302495 (918)	total: 7.09s	remaining: 625ms
919:	learn: 0.2026895	test: 0.2302455	best: 0.2302455 (919)	total: 7.09s	remaining: 617ms
920:	learn: 0.2026660	test: 0.2302287	best: 0.2302287 (920)	total: 7.1s	remaining: 609ms
921:	learn: 0.2026478	test: 0.2302284	best: 0.2302284 (921)	total: 7.11s	remaining: 601ms
922:	learn: 0.2026229	test: 0.2302159	best: 0.2302159 (922)	total: 7.12s	remaining: 594ms
923:	learn: 0.2026167	test: 0.2302153	best: 0.2302153 (923)	total: 7.12s	remaining: 586ms
924:	learn: 0.2025967	test: 0.2301962	best: 0.2301962 (924)	total: 7.13s	remaining: 578ms
925:	learn:

In [318]:
sub = sub.sort_values(by=['id'])
sub['demand'] = np.exp(sub['demand']) - 1

for i in range(sub.shape[0]):
    if sub.iloc[i,1] < 0:
        sub.iloc[i,1] = 0
        
sub = sub.astype({'id':'int'})
sub

id    demand
0      601  0.211119
1      697  0.211119
2      831  0.211119
3      875  0.211119
0      975  0.211119
..     ...       ...
2   407111  0.211119
3   407113  0.211119
0   407287  0.211119
0   407289  0.211119
0   407293  0.211119

[4693 rows x 2 columns]

In [294]:
sub.to_csv('lt_sample_submission_11.csv', index=False) #каждый магаз отдельно катбуст

In [53]:
sub = pd.DataFrame({'id': test_id_list, 'demand': final_pred}) 
sub['demand'] = np.exp(sub['demand']) - 1
sub.head()

id    demand
0  601  0.614682
1  697  0.615466
2  831  0.604010
3  875  1.063882
4  975  0.610611

In [54]:
sub.to_csv('lt_sample_submission_8.csv', index=False) # катбуст